In [7]:
from bs4 import BeautifulSoup as bs4
import requests
import pandas as pd
import re
import time
from selenium import webdriver
from selenium.webdriver.common.keys import Keys

from webdriver_manager.chrome import ChromeDriverManager

pages=[]

urls= set()

In [8]:
url = "https://www.partilhei.com/"
no_more_pages = False
while(not(no_more_pages)):
    current_url = url
    print(current_url)
    print('--------------------------')
    page = requests.get(current_url)
    soup = bs4(page.text, 'html.parser')

    try:
        link_elements = soup.find_all("h2")
        for link_element in link_elements:
            links = link_element.findAll('a')
            for link in links:
                article_link = link.get('href')
                print('article link:',article_link)
                urls.add(article_link)
        
        button_link = ""
        button_element = soup.find_all('div', class_ = 'nav-previous')
        for link_element in button_element:
            links = link_element.findAll('a')
            for link in links:
                button_link = link.get('href')
                print('previous button link:',button_link)
                
        if button_link != "":
            url = button_link
        else:
            no_more_pages = True # ADAPT

    except:
        pass

    time.sleep(3)

https://www.partilhei.com/
--------------------------
article link: https://www.partilhei.com/judite-sousa-na-guerra-na-ucrania-sem-dinheiro-para-comer
article link: https://www.partilhei.com/um-dia-na-vida-de-um-portugues
article link: https://www.partilhei.com/deputado-do-chega-para-assessor-do-ps-parto-te-a-tromba-es-um-anao
article link: https://www.partilhei.com/encontrados-sacos-de-sangue-e-seringas-no-hotel-onde-a-equipa-da-w52-fc-porto-estagiou
article link: https://www.partilhei.com/vizela-mulher-da-entrada-nas-urgencias-com-7-zaragatoas-na-vagina
article link: https://www.partilhei.com/facebook-instagram-e-whatsapp-em-baixo-vice-almirante-gouveia-e-melo-chamado-para-repor-a-ordem
article link: https://www.partilhei.com/nova-lei-autoriza-os-homens-a-sairem-com-os-amigos-sem-autorizacao-das-mulheres
article link: https://www.partilhei.com/teste-simples-para-criancas-mas-para-alguns-adultos-e-um-quebra-cabecas
article link: https://www.partilhei.com/isto-meus-amigos-e-a-triste-r

In [121]:
len(urls)

2809

In [124]:
driver = webdriver.Chrome(ChromeDriverManager().install())

In [118]:
# urls_test = [
#     "https://www.partilhei.com/burrices-engracadas-mas-tristes-de-doentes-relatado",
#     "https://www.partilhei.com/como-e-que-um-homem-escolhe-uma-mulher",
#     "https://www.partilhei.com/ultima-hora-aluno-da-casa-pia-confessa-ter-mentido-sobre-carlos-cruz",
#     "https://www.partilhei.com/luciana-abreu-compara-a-mae-e-a-irma-a-um-cao-e-diz-e-um-exemplo-duro-eu-sei",
#     "https://www.partilhei.com/bombeiro-heroi-trava-morte-na-ponte-sobre-a-a4-em-valongo",
#     "https://www.partilhei.com/vizela-mulher-da-entrada-nas-urgencias-com-7-zaragatoas-na-vagina",
# ]

In [125]:
from selenium.webdriver.common.action_chains import ActionChains

titles=[]
texts=[]
sources=[]
df_urls = []

# Initialize an empty dataframe
df = pd.DataFrame(columns=['Title', 'Text', 'Source', 'URL'])

for url in urls:

    news_title = 'NONE'
    news_text = 'NONE'
    news_source = 'NONE'
    news_categories = []
    news_tags = []
    fictional_article = False

    # Open webpage
    driver.get(url)
    print(url)

    # Extract first 10 article URLs
    soup = bs4(driver.page_source, 'html.parser')

    # Press button to load more news articles if it exists
    button_element_href = ''
    try:
        button_element_href = soup.find('div', class_ = 'continuarbtn').find('a').get('href')
    except:
        pass
    
    time.sleep(1.5)
    print("button_href:",button_element_href)
    if button_element_href != '':
        # An ad is blocking the content, so we must deal with it first
        # Find the h1 element of the title
        element = driver.find_element_by_tag_name("h1")

        # Create an ActionChains instance
        actions = ActionChains(driver)

        # Move the mouse to the center of the element
        actions.move_to_element(element).perform()

        # Click at the center of the element, which will 
        actions.click().perform()

        # Switch to the new tab opened by the ad
        driver.switch_to.window(driver.window_handles[-1])

        # Close the new tab
        driver.close()

        # Switch back to the initial tab with the news article
        driver.switch_to.window(driver.window_handles[0])

        # Click on the button to load more text
        driver.find_element_by_class_name("continuarbtn").click()

    # Extract article's data
    try:
        title = soup.find('h1').get_text()

        cats_div = soup.find('div', class_='post-info')
        if cats_div:
            news_categories = [cat.get_text(strip=True).lower() for cat in cats_div.find_all('a')]
            print(news_categories)
        else:
            print("No tags found.")

        tags_div = soup.find('div', class_='tags')
        if tags_div:
            news_tags = [tag.get_text(strip=True).lower() for tag in tags_div.find_all('a')]
            print(news_tags)
        else:
            print("No tags found.")
        
        if 'anedotas' not in news_categories:
            news_title = soup.find("h1").get_text().strip()

            paragraphs = soup.find_all("p")
            news_text = "\n".join(p.get_text() for p in paragraphs)
            lowercase_text = news_text.lower()

            ler_mais_div = soup.find("div", id="lermais")
            if ler_mais_div is not None:
                if ler_mais_div.find("p"):
                    # All the 'p' tags include the whole text
                    pass
                else:
                    ler_mais_text = ler_mais_div.get_text()

                news_text += ler_mais_text

            source_div = soup.find('div', style='float:right;font-size:xx-small')
            if source_div is not None:
                news_source = source_div.text.lower().split('fonte:')[-1].strip()
            else:
                news_source = "n/a"

            news_text = news_text.strip()
            lines = news_text.splitlines()

            # If the news article states that it's a fictional story for entertaining purposes, it isn't considered fake news
            stripped_line = lines[-1].strip()
            if "Nota: Artigo fictício/satírico/humorístico. A informação aqui veiculada não corresponde à realidade, é meramente ficcional." in stripped_line:
                fictional_article = True

            # Join the lines back into a string
            news_text = '\n'.join(lines).lstrip()
            news_text = re.sub(r'\n+', '\n', news_text) # Replace consecutive paragraphs with a single one
            news_text = re.sub(r'\t', '', news_text) # Replace consecutive paragraphs with a single one

            if not(fictional_article):
                titles.append(news_title)
                texts.append(news_text)
                sources.append(news_source)
                df_urls.append(url)
            else:
                print("*********** Fictional Article! ***********")

            print(news_title)
            print(news_text)
            print(news_source)

    except:
        pass

    time.sleep(3)

# Create a new dataframe from the lists
new_data = pd.DataFrame({'Title': titles, 'Text': texts, 'Source': sources, 'URL': df_urls})

# Concatenate the new dataframe with the existing dataframe
df = pd.concat([df, new_data], ignore_index=True)

https://www.partilhei.com/ultima-hora-encontrada-bomba-na-nazare
button_href: 
['portugal']
['alerta', 'noticias', 'portugal', 'ultima hora']
ULTIMA HORA: Encontrada bomba na Nazaré
Uma embarcação de pesca encontrou, nesta segunda-feira, uma bomba durante a faina, ao largo da Nazaré, cerca das 9 horas. O engenho foi trazido para terra para observação pela Marinha no Porto da Nazaré. 
Foi, entretanto, detonado, “em segurança”, por uma equipa de mergulhadores da Marinha, especializada em inativação de explosivos, a uma distância mínima de mil metros da costa, confirmou a TVI no local.
A bomba, em elevado estado de corrosão, tem mais de 202 quilos de H6, um explosivo equivalente a 600 quilos de TNT [trinitrotolueno], e não dispõe de qualquer indicação que o identifique.
A Marinha tinha confirmado à TVI que, “numa primeira análise”, seria “uma bomba de avião”, que provavelmente estaria obsoleta. Como o engenho teria “o equivalente a 600 quilos de TNT”, a situação inspirava “alguns cuidados

TimeoutException: Message: timeout: Timed out receiving message from renderer: 299.664
  (Session info: chrome=114.0.5735.135)


In [136]:
len(urls)

2809

In [127]:
len(titles)

2522

In [128]:
len(texts)

2522

In [129]:
len(df_urls)

2522

In [131]:
# The driver crashed, let's save the data into two different datasets

# Create a new dataframe from the lists
new_data = pd.DataFrame({'Title': titles, 'Text': texts, 'Source': sources, 'URL': df_urls})

# Concatenate the new dataframe with the existing dataframe
df = pd.concat([df, new_data], ignore_index=True)

In [132]:
df.head()

Title  \
0            ULTIMA HORA: Encontrada bomba na Nazaré   
1  Nem vais acreditar quando souberes onde Johnny...   
2  Vais ficar chocado com a vida trágica e heróic...   
3  O filho desmontou a bancada do falecido pai… O...   
4          Cuidado Netflix, que a bolha vai rebentar   

                                                Text    Source  \
0  Uma embarcação de pesca encontrou, nesta segun...       n/a   
1  Antigos agentes do ator de Hollywood revelam t...       n/a   
2  Quem não se lembra de Keanu Reeves, o ator que...       n/a   
3  Após a morte do seu pai, o filho decidiu desmo...       n/a   
4  Tamanho é o investimento na compra de conteúdo...  expresso   

                                                 URL  
0  https://www.partilhei.com/ultima-hora-encontra...  
1  https://www.partilhei.com/nem-vais-acreditar-q...  
2  https://www.partilhei.com/vais-ficar-chocado-c...  
3  https://www.partilhei.com/o-filho-desmontou-a-...  
4  https://www.partilhei.com/cuidado-netflix-que-...

In [133]:
df.head()
df.to_csv("Partilhei_com_dataset_p1.csv", index=False)

In [155]:
df_p1 = pd.read_csv("Partilhei_com_dataset_p1.csv")
df_p1.head()

Title  \
0            ULTIMA HORA: Encontrada bomba na Nazaré   
1  Nem vais acreditar quando souberes onde Johnny...   
2  Vais ficar chocado com a vida trágica e heróic...   
3  O filho desmontou a bancada do falecido pai… O...   
4          Cuidado Netflix, que a bolha vai rebentar   

                                                Text    Source  \
0  Uma embarcação de pesca encontrou, nesta segun...       NaN   
1  Antigos agentes do ator de Hollywood revelam t...       NaN   
2  Quem não se lembra de Keanu Reeves, o ator que...       NaN   
3  Após a morte do seu pai, o filho decidiu desmo...       NaN   
4  Tamanho é o investimento na compra de conteúdo...  expresso   

                                                 URL  
0  https://www.partilhei.com/ultima-hora-encontra...  
1  https://www.partilhei.com/nem-vais-acreditar-q...  
2  https://www.partilhei.com/vais-ficar-chocado-c...  
3  https://www.partilhei.com/o-filho-desmontou-a-...  
4  https://www.partilhei.com/cuidado-netflix-que-...

In [135]:
for source in set(df['Source']):
    print(source)

bang
impala.pt
hugogil
historiascomvalor
sic
portaldaqueixa
direção de serviços do irs
apodrecetuga
manifesto74.pt
doidices.net
deco
automoveis-online
visao
muitofixe
fatosdesconhecidos
sic noticias
maxmen
jornalportugal
dr.arthur frazão (médico)
saude.com
insider.pro
quiosquedigital
circulaseguro
carlos paz professor economia
fontes:  instagram de ines helen / playboy.pt / soparahomens
jn*
like3za
jn
naturalnews.com
notícias ao minuto
ojogo
tribunaexpresso
24.sapo.pt
exameinformatica
altamente
portalbeleza
paulo vaz‎-motoristas lusitanos
exame
vaidarzebra
deco-proteste
f.c.p.
the times
jornalq
expresso
msn noticias
telecinco.es
jornal noticias
noticiasaominuto
tugasports
geringonca
público
tv7dias
discovery
cmjornal.pt
jornaleconomico.sapo.pt
visão
zap.aeiou.pt
esquerda.net
reuters/claus fisker/scanpix
facebook de marcel silva junior
ptjornal
imprensafalsa.com
msn
rebentaabolha.net
naoegrandepistola
maisopiniao
g1
visao.sapo.pt
luminaria
informamais.pt
daily mail uk
porfalarnoutracois

In [137]:
urls_backup = set(urls)

In [138]:
len(urls_backup)

2809

In [149]:
# Remove the extracted articles of the df in the urls set

# Convert the urls set into a list
urls_list = list(urls)

In [150]:
len(urls_list)

2809

In [151]:
# Create a set of the URLs from the saved dataset
saved_urls = set(df_p1['URL'])

In [152]:
# Create a list of remaining URLs by finding the difference between the full list and the saved URLs
remaining_urls = list(set(urls_list) - saved_urls)

In [159]:
# Print the length of remaining_urls
print(len(remaining_urls))

287


In [154]:
for url in remaining_urls:
    print(url)

https://www.partilhei.com/diva-e-m%ce%b1ric%ce%b1s-e-o-que-uma-jornalista-suica-chama-a-cristiano-ronaldo
https://www.partilhei.com/andas-na-estrada-cuidado-com-os-acessos-de-raiva-de-com-quem-te-cruzas
https://www.partilhei.com/erica-fontes-oferece-noite-escaldante-como-recompensa-a-quem-encontrar-pedro-dias
https://www.partilhei.com/mae-brasileira-da-a-luz-quadrigemeos-estao-todos-bem-de-saude
https://www.partilhei.com/anaconda-e-encontrada-com-a-refeicao-invulgar-dentro-da-barriga
https://www.partilhei.com/luto-no-mundo-gospel-cantora-morre-apos-gravissimo-acidente
https://www.partilhei.com/costumas-espremer-borbulhas-para-ja-de-o-fazer-pode-ser-fatal
https://www.partilhei.com/uma-loira-que-vai-para-toronto-mas-nao-quer-ir-na-classe-economica-e
https://www.partilhei.com/a-gata-de-goucha-faz-algo-inedito-para-matar-saudades-do-dono
https://www.partilhei.com/se-vais-tirar-a-carta-tem-cuidado-exames-de-conducao-serao-vigiados-em-2017
https://www.partilhei.com/o-dia-em-que-o-preco-certo

In [160]:
driver = webdriver.Chrome(ChromeDriverManager().install())

In [161]:
from selenium.webdriver.common.action_chains import ActionChains

titles=[]
texts=[]
sources=[]
df_urls = []

# Initialize an empty dataframe
df = pd.DataFrame(columns=['Title', 'Text', 'Source', 'URL'])

for url in remaining_urls:

    news_title = 'NONE'
    news_text = 'NONE'
    news_source = 'NONE'
    news_categories = []
    news_tags = []
    fictional_article = False

    # Open webpage
    driver.get(url)
    print(url)

    # Extract first 10 article URLs
    soup = bs4(driver.page_source, 'html.parser')

    # Press button to load more news articles if it exists
    button_element_href = ''
    try:
        button_element_href = soup.find('div', class_ = 'continuarbtn').find('a').get('href')
    except:
        pass
    
    time.sleep(1.5)
    print("button_href:",button_element_href)
    if button_element_href != '':
        # An ad is blocking the content, so we must deal with it first
        # Find the h1 element of the title
        element = driver.find_element_by_tag_name("h1")

        # Create an ActionChains instance
        actions = ActionChains(driver)

        # Move the mouse to the center of the element
        actions.move_to_element(element).perform()

        # Click at the center of the element, which will 
        actions.click().perform()

        # Switch to the new tab opened by the ad
        driver.switch_to.window(driver.window_handles[-1])

        # Close the new tab
        driver.close()

        # Switch back to the initial tab with the news article
        driver.switch_to.window(driver.window_handles[0])

        # Click on the button to load more text
        driver.find_element_by_class_name("continuarbtn").click()

    # Extract article's data
    try:
        title = soup.find('h1').get_text()

        cats_div = soup.find('div', class_='post-info')
        if cats_div:
            news_categories = [cat.get_text(strip=True).lower() for cat in cats_div.find_all('a')]
            print(news_categories)
        else:
            print("No tags found.")

        tags_div = soup.find('div', class_='tags')
        if tags_div:
            news_tags = [tag.get_text(strip=True).lower() for tag in tags_div.find_all('a')]
            print(news_tags)
        else:
            print("No tags found.")
        
        if 'anedotas' not in news_categories:
            news_title = soup.find("h1").get_text().strip()

            paragraphs = soup.find_all("p")
            news_text = "\n".join(p.get_text() for p in paragraphs)
            lowercase_text = news_text.lower()

            ler_mais_div = soup.find("div", id="lermais")
            if ler_mais_div is not None:
                if ler_mais_div.find("p"):
                    # All the 'p' tags include the whole text
                    pass
                else:
                    ler_mais_text = ler_mais_div.get_text()

                news_text += ler_mais_text

            source_div = soup.find('div', style='float:right;font-size:xx-small')
            if source_div is not None:
                news_source = source_div.text.lower().split('fonte:')[-1].strip()
            else:
                news_source = "n/a"

            news_text = news_text.strip()
            lines = news_text.splitlines()

            # If the news article states that it's a fictional story for entertaining purposes, it isn't considered fake news
            stripped_line = lines[-1].strip()
            if "Nota: Artigo fictício/satírico/humorístico. A informação aqui veiculada não corresponde à realidade, é meramente ficcional." in stripped_line:
                fictional_article = True

            # Join the lines back into a string
            news_text = '\n'.join(lines).lstrip()
            news_text = re.sub(r'\n+', '\n', news_text) # Replace consecutive paragraphs with a single one
            news_text = re.sub(r'\t', '', news_text) # Replace consecutive paragraphs with a single one

            if not(fictional_article):
                titles.append(news_title)
                texts.append(news_text)
                sources.append(news_source)
                df_urls.append(url)
            else:
                print("*********** Fictional Article! ***********")

            print(news_title)
            print(news_text)
            print(news_source)

    except:
        pass

    time.sleep(3)

# Create a new dataframe from the lists
new_data = pd.DataFrame({'Title': titles, 'Text': texts, 'Source': sources, 'URL': df_urls})

# Concatenate the new dataframe with the existing dataframe
df = pd.concat([df, new_data], ignore_index=True)

https://www.partilhei.com/diva-e-m%ce%b1ric%ce%b1s-e-o-que-uma-jornalista-suica-chama-a-cristiano-ronaldo
button_href: 
['polémica']
['desporto', 'futebol', 'polemica', 'triste']
Diva e mαricαs é o que uma jornalista Suíça chama a Cristiano Ronaldo
Andrea Vetsch, jornalista suíça, protagonizou um duro ataque a Cristiano Ronaldo, em direto na SRF (Swiss Radio and Television).
“Ronaldo entrou no relvado com o cabelo perfeitamente penteado e cheio de gel, sobrancelhas perfeitamente aparadas e um corpo totalmente depilado”, começou por dizer, em tom irónico.
De seguida, Andrea Vetsch retirou do ‘baú’ o Portugal-Holanda, do Campeonato Europeu de 2012, quando o capitão português mudou de penteado ao intervalo, para dar a ‘machadada’ final.
“A diva até voltou do relvado com um penteado completamente diferente depois do intervalo. Estes homens, a quem alguns chamam “mαricαs”, estão, agora, de saída do futebol”, atirou, para passar a elogiar a seleção… islandesa.
“Os verdadeiros homens voltaram

In [162]:
df.head()
df.to_csv("Partilhei_com_dataset_p2.csv", index=False)

In [163]:
df_p2 = pd.read_csv("Partilhei_com_dataset_p2.csv")
df_p2.head()

Title  \
0  Diva e mαricαs é o que uma jornalista Suíça ch...   
1  Andas na estrada? Cuidado com os acessos de ra...   
2  Érica Fontes oferece noite escaldante como rec...   
3  Mãe brasileira dá à luz quadrigémeos. Estão to...   
4  Anaconda é encontrada com a refeição invulgar ...   

                                                Text       Source  \
0  Andrea Vetsch, jornalista suíça, protagonizou ...          NaN   
1  A polícia britânica divulgou esta terça-feira,...  sicnoticias   
2  Érica Fontes veio hoje a público lançar uma of...          NaN   
3  Cristiele Souza, de 34 anos, deu à luz quadrig...          NaN   
4  Eles encontraram esta anaconda morta depois de...          NaN   

                                                 URL  
0  https://www.partilhei.com/diva-e-m%ce%b1ric%ce...  
1  https://www.partilhei.com/andas-na-estrada-cui...  
2  https://www.partilhei.com/erica-fontes-oferece...  
3  https://www.partilhei.com/mae-brasileira-da-a-...  
4  https://www.partilhei.com/anaconda-e-encontrad...